In [17]:
import json
import pandas as pd
import shutil
import os
import numpy as np
import torch
import joblib
from deepface import DeepFace
from pydub import AudioSegment
from pydub.utils import make_chunks
import os, re

In [5]:
file = pandas.read_csv('../../Speech-Emotion-Recognition/features/6-category/train_opensmile_savee_ravdess.csv')

In [6]:
file.head()

label      1    2         3         4         5         6         7  \
0      0  186.0  0.0  0.171480 -0.000036  0.178284  0.183930  0.051256   
1      0  123.0  0.0  0.132264 -0.000034  0.138557  0.137833  0.027193   
2      0  123.0  0.0  0.243441  0.000119  0.220708  0.260290  0.104235   
3      0  267.0  0.0  0.243272  0.000321  0.181067  0.259608  0.111849   
4      0  115.0  0.0  0.094286 -0.000044  0.102221  0.098318  0.015882   

          8         9  ...      1573      1574      1575      1576      1577  \
0  0.226432  1.555656  ...  0.000007  0.000137  0.000199  0.000130  0.000329   
1  0.164943  1.181051  ... -0.000019  0.000145  0.000272  0.000164  0.000436   
2  0.323122  1.296685  ...  0.000009  0.000149  0.000155  0.000140  0.000295   
3  0.336371  1.590986  ... -0.000014  0.000088  0.000137  0.000102  0.000240   
4  0.126109  1.827586  ... -0.000003  0.000151  0.000138  0.000153  0.000291   

       1578      1579      1580      1581  1582  
0  0.002123  0.981928  0.945783  2.083333  3.84  
1  0.002027  0.978102  0.970803  2.695418  3.71  
2  0.003037  0.005682  0.005682  3.125000  3.84  
3  0.001614  0.010929  0.005464  2.813299  3.91  
4  0.002370  0.018634  0.006211  3.021978  3.64  

[5 rows x 1583 columns]

In [8]:
label = file.label

In [9]:
label.unique()

array([0, 1, 2, 3, 4, 5])

In [3]:
path_r = "../../Speech-Emotion-Recognition/datasets/ravdess"
labels = ["neutral", "calm", "happy", "sad", "angry", "fearful", "disgust", "surprised"]

In [31]:
for i in range(1, 25):
    filepath = os.path.join(path_r, "Actor_" + str(i).zfill(2))
    print("processing", filepath)
    assert os.path.isdir(filepath)
    for file in os.listdir(filepath):
        label = file.strip('.wav').split('-')[2]
        file_move = os.path.join(path_r, labels[int(label) - 1])
        print("moving", file, "to", file_move)
        if not os.path.isdir(file_move):
            os.makedirs(file_move)
        shutil.copyfile(os.path.join(filepath, file), os.path.join(file_move, file))

processing ../../Speech-Emotion-Recognition/datasets/ravdess/Actor_01
moving 03-01-04-02-01-01-01.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/sad
moving 03-01-03-02-02-02-01.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/happy
moving 03-01-08-02-02-02-01.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/surprised
moving 03-01-05-01-02-02-01.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/angry
moving 03-01-05-01-02-01-01.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/angry
moving 03-01-02-02-01-02-01.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/calm
moving 03-01-04-01-01-02-01.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/sad
moving 03-01-06-02-02-01-01.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/fearful
moving 03-01-05-02-01-01-01.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/angry
moving 03-01-08-02-02-01-01.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/surprised
moving 03-01-05

moving 03-01-07-02-02-01-02.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/disgust
moving 03-01-07-02-01-02-02.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/disgust
moving 03-01-02-02-02-02-02.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/calm
moving 03-01-07-01-01-02-02.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/disgust
moving 03-01-01-01-02-02-02.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/neutral
moving 03-01-04-02-02-01-02.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/sad
moving 03-01-07-01-02-01-02.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/disgust
moving 03-01-05-02-02-02-02.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/angry
moving 03-01-04-02-01-01-02.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/sad
moving 03-01-08-01-02-02-02.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/surprised
moving 03-01-05-01-02-02-02.wav to ../../Speech-Emotion-Recognition/datasets/ravd

moving 03-01-07-02-02-02-04.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/disgust
moving 03-01-07-01-01-02-04.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/disgust
moving 03-01-05-01-02-02-04.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/angry
moving 03-01-02-01-02-01-04.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/calm
moving 03-01-02-02-02-02-04.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/calm
moving 03-01-07-02-01-02-04.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/disgust
moving 03-01-08-01-01-01-04.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/surprised
moving 03-01-04-01-02-01-04.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/sad
moving 03-01-01-01-01-02-04.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/neutral
moving 03-01-04-01-02-02-04.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/sad
moving 03-01-08-02-01-02-04.wav to ../../Speech-Emotion-Recognition/datasets/ravdess

moving 03-01-06-01-02-02-06.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/fearful
moving 03-01-05-02-02-01-06.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/angry
moving 03-01-04-02-01-01-06.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/sad
moving 03-01-02-01-01-02-06.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/calm
moving 03-01-07-01-01-02-06.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/disgust
moving 03-01-01-01-01-02-06.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/neutral
moving 03-01-02-02-02-02-06.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/calm
moving 03-01-07-02-01-02-06.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/disgust
moving 03-01-08-01-01-02-06.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/surprised
moving 03-01-05-01-01-02-06.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/angry
moving 03-01-08-01-02-02-06.wav to ../../Speech-Emotion-Recognition/datasets/ravde

moving 03-01-04-02-01-02-08.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/sad
moving 03-01-02-01-01-01-08.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/calm
moving 03-01-06-02-02-01-08.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/fearful
moving 03-01-04-01-02-01-08.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/sad
moving 03-01-03-02-02-01-08.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/happy
moving 03-01-06-01-02-01-08.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/fearful
moving 03-01-03-02-02-02-08.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/happy
moving 03-01-08-01-02-02-08.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/surprised
moving 03-01-04-02-02-02-08.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/sad
moving 03-01-02-02-01-02-08.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/calm
moving 03-01-04-01-01-02-08.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/sad
m

...

moving 03-01-01-01-02-02-17.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/neutral
moving 03-01-04-02-02-01-17.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/sad
moving 03-01-01-01-01-02-17.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/neutral
moving 03-01-02-01-02-01-17.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/calm
moving 03-01-05-02-02-01-17.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/angry
moving 03-01-03-02-02-02-17.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/happy
moving 03-01-08-01-02-02-17.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/surprised
moving 03-01-07-02-02-02-17.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/disgust
moving 03-01-05-02-01-02-17.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/angry
moving 03-01-04-02-01-02-17.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/sad
moving 03-01-06-01-02-02-17.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/

moving 03-01-03-01-01-02-18.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/happy
moving 03-01-01-01-02-01-18.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/neutral
moving 03-01-06-02-02-02-18.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/fearful
processing ../../Speech-Emotion-Recognition/datasets/ravdess/Actor_19
moving 03-01-02-02-02-01-19.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/calm
moving 03-01-06-01-01-02-19.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/fearful
moving 03-01-08-02-01-02-19.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/surprised
moving 03-01-08-02-02-01-19.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/surprised
moving 03-01-08-02-02-02-19.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/surprised
moving 03-01-01-01-02-02-19.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/neutral
moving 03-01-04-01-01-02-19.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/sad
mov

moving 03-01-01-01-01-02-20.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/neutral
moving 03-01-03-02-02-02-20.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/happy
moving 03-01-03-02-01-01-20.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/happy
moving 03-01-04-02-01-02-20.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/sad
moving 03-01-04-01-01-02-20.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/sad
moving 03-01-04-01-01-01-20.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/sad
moving 03-01-08-02-02-01-20.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/surprised
moving 03-01-03-02-02-01-20.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/happy
moving 03-01-08-02-02-02-20.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/surprised
moving 03-01-01-01-02-01-20.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/neutral
moving 03-01-05-01-02-02-20.wav to ../../Speech-Emotion-Recognition/datasets/ravdess

moving 03-01-04-02-02-02-22.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/sad
moving 03-01-08-01-02-01-22.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/surprised
moving 03-01-06-02-02-02-22.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/fearful
moving 03-01-04-01-02-02-22.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/sad
moving 03-01-06-02-01-01-22.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/fearful
moving 03-01-04-01-01-01-22.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/sad
moving 03-01-02-02-01-01-22.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/calm
moving 03-01-07-02-01-02-22.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/disgust
moving 03-01-01-01-01-02-22.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/neutral
moving 03-01-06-01-01-01-22.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/fearful
moving 03-01-04-02-02-01-22.wav to ../../Speech-Emotion-Recognition/datasets/ravdes

moving 03-01-05-01-01-01-24.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/angry
moving 03-01-05-01-02-01-24.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/angry
moving 03-01-06-02-01-01-24.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/fearful
moving 03-01-03-01-01-02-24.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/happy
moving 03-01-06-01-02-01-24.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/fearful
moving 03-01-06-01-01-01-24.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/fearful
moving 03-01-05-01-01-02-24.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/angry
moving 03-01-01-01-02-02-24.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/neutral
moving 03-01-08-02-01-02-24.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/surprised
moving 03-01-03-02-01-02-24.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/happy
moving 03-01-07-02-01-01-24.wav to ../../Speech-Emotion-Recognition/datasets/r

In [12]:
file_action = json.load(open('../data/memor_2.json'))

In [14]:
action = file_action[0]
action_0 = action['clips'][0]
print(action_0['segment'], action_0['label'])
scores = torch.Tensor(action_0['scores'])
scores_norm = torch.nn.functional.softmax(scores, dim=0)

scores_norm.max()

[1, 16] brushing hair


tensor(0.2186)

In [16]:
label_action = list()
for item in file_action:
    name_video = item['video']
    name_actions = list()
    print(name_video)
    for segment in item['clips']:
        scores_norm = torch.nn.functional.softmax(torch.Tensor(segment['scores']), dim=0)
        if scores_norm.max() > 0:
            name_actions.append(segment['label'])
            print(segment['label'], scores_norm.max())
        
    label_action.append((name_video, name_actions))

S01E01_000.mp4
brushing hair tensor(0.2186)
brushing hair tensor(0.2389)
brushing hair tensor(0.3595)
contact juggling tensor(0.2577)
checking tires tensor(0.0765)
checking tires tensor(0.0749)
blasting sand tensor(0.0845)
blasting sand tensor(0.2126)
checking tires tensor(0.0718)
blasting sand tensor(0.0517)
drawing tensor(0.0935)
cracking neck tensor(0.3498)
cartwheeling tensor(0.0681)
drawing tensor(0.0715)
cooking chicken tensor(0.0640)
cleaning gutters tensor(0.0622)
dribbling basketball tensor(0.1057)
cleaning gutters tensor(0.1249)
cleaning gutters tensor(0.2400)
cleaning gutters tensor(0.1234)
cleaning gutters tensor(0.1116)
clean and jerk tensor(0.0689)
drawing tensor(0.1408)
cleaning gutters tensor(0.2327)
cleaning gutters tensor(0.2564)
cleaning gutters tensor(0.6030)
S01E01_001.mp4
cleaning windows tensor(0.1658)
cleaning windows tensor(0.2024)
cleaning gutters tensor(0.1202)
cleaning gutters tensor(0.1146)
drawing tensor(0.0906)
cleaning gutters tensor(0.2716)
cleaning gut

air drumming tensor(0.1530)
bandaging tensor(0.0698)
air drumming tensor(0.1137)
air drumming tensor(0.1008)
air drumming tensor(0.1127)
bandaging tensor(0.1040)
bandaging tensor(0.0937)
abseiling tensor(0.1434)
abseiling tensor(0.2573)
abseiling tensor(0.2753)
abseiling tensor(0.2987)
air drumming tensor(0.2040)
air drumming tensor(0.2824)
abseiling tensor(0.2454)
breading or breadcrumbing tensor(0.1991)
blowing nose tensor(0.1212)
clean and jerk tensor(0.1141)
cleaning gutters tensor(0.0739)
abseiling tensor(0.1248)
cleaning gutters tensor(0.1867)
S01E01_016.mp4
air drumming tensor(0.1373)
clean and jerk tensor(0.0973)
cleaning windows tensor(0.0626)
abseiling tensor(0.1022)
cleaning toilet tensor(0.1314)
cleaning toilet tensor(0.1870)
cleaning windows tensor(0.1164)
clean and jerk tensor(0.1015)
abseiling tensor(0.0980)
abseiling tensor(0.0848)
cleaning windows tensor(0.0899)
air drumming tensor(0.0949)
abseiling tensor(0.0596)
abseiling tensor(0.1179)
abseiling tensor(0.1375)
banda

abseiling tensor(0.1975)
air drumming tensor(0.1490)
air drumming tensor(0.3441)
air drumming tensor(0.1916)
air drumming tensor(0.2821)
air drumming tensor(0.0954)
baby waking up tensor(0.4405)
baby waking up tensor(0.3474)
bandaging tensor(0.3081)
cleaning toilet tensor(0.1452)
bandaging tensor(0.1354)
bandaging tensor(0.1517)
bandaging tensor(0.0867)
S01E01_035.mp4
bandaging tensor(0.0815)
cleaning windows tensor(0.1102)
cleaning windows tensor(0.3118)
cleaning windows tensor(0.1664)
cleaning windows tensor(0.1427)
air drumming tensor(0.0706)
abseiling tensor(0.1610)
air drumming tensor(0.0621)
air drumming tensor(0.0619)
cleaning gutters tensor(0.0723)
air drumming tensor(0.1246)
abseiling tensor(0.0382)
dribbling basketball tensor(0.2914)
S01E01_036.mp4
checking tires tensor(0.1366)
answering questions tensor(0.1219)
drinking tensor(0.0932)
cleaning gutters tensor(0.0364)
answering questions tensor(0.0677)
cleaning gutters tensor(0.1563)
cleaning gutters tensor(0.2337)
S01E01_037.

clapping tensor(0.0653)
cleaning shoes tensor(0.0756)
S01E02_014.mp4
cleaning shoes tensor(0.8265)
clapping tensor(0.1513)
checking tires tensor(0.1881)
checking tires tensor(0.1929)
changing wheel tensor(0.1426)
cleaning shoes tensor(0.6045)
checking tires tensor(0.1767)
breakdancing tensor(0.0845)
dribbling basketball tensor(0.4428)
clapping tensor(0.1357)
clapping tensor(0.1518)
cleaning toilet tensor(0.0472)
bandaging tensor(0.0547)
cleaning windows tensor(0.0644)
cleaning shoes tensor(0.0566)
clapping tensor(0.0995)
bandaging tensor(0.0658)
bandaging tensor(0.1014)
air drumming tensor(0.3403)
bench pressing tensor(0.1685)
air drumming tensor(0.2738)
changing wheel tensor(0.3308)
changing wheel tensor(0.1094)
S01E02_015.mp4
clapping tensor(0.1044)
air drumming tensor(0.0692)
bandaging tensor(0.0967)
air drumming tensor(0.3191)
bench pressing tensor(0.1750)
air drumming tensor(0.2561)
changing wheel tensor(0.3116)
changing wheel tensor(0.1142)
changing wheel tensor(0.0794)
cleaning 

clean and jerk tensor(0.1330)
air drumming tensor(0.1076)
clean and jerk tensor(0.1381)
bandaging tensor(0.1543)
cleaning gutters tensor(0.1996)
S01E02_035.mp4
cleaning windows tensor(0.1299)
cleaning windows tensor(0.0664)
bandaging tensor(0.1441)
abseiling tensor(0.0657)
clean and jerk tensor(0.1378)
clean and jerk tensor(0.0617)
changing wheel tensor(0.1159)
bench pressing tensor(0.1171)
bench pressing tensor(0.1216)
bench pressing tensor(0.1716)
bench pressing tensor(0.1057)
bandaging tensor(0.1180)
bandaging tensor(0.1436)
clapping tensor(0.2067)
breading or breadcrumbing tensor(0.0785)
bandaging tensor(0.2111)
S01E02_036.mp4
cleaning windows tensor(0.1235)
bandaging tensor(0.3279)
clapping tensor(0.1521)
clapping tensor(0.1117)
bandaging tensor(0.1355)
checking tires tensor(0.3075)
clapping tensor(0.1784)
checking tires tensor(0.2119)
checking tires tensor(0.3702)
clapping tensor(0.1329)
brushing teeth tensor(0.0756)
cracking neck tensor(0.0772)
clapping tensor(0.1756)
cracking n

...

changing wheel tensor(0.1678)
changing wheel tensor(0.1812)
S09E21_018.mp4
bandaging tensor(0.1841)
bandaging tensor(0.2351)
bandaging tensor(0.3939)
bandaging tensor(0.4922)
bandaging tensor(0.2626)
bandaging tensor(0.1588)
clean and jerk tensor(0.1719)
clean and jerk tensor(0.1168)
clean and jerk tensor(0.1379)
cleaning windows tensor(0.1879)
changing wheel tensor(0.1683)
changing wheel tensor(0.1657)
changing wheel tensor(0.2066)
bandaging tensor(0.1726)
clean and jerk tensor(0.2903)
clean and jerk tensor(0.0980)
clean and jerk tensor(0.2250)
S09E21_019.mp4
bandaging tensor(0.1757)
bandaging tensor(0.2251)
bandaging tensor(0.1709)
cleaning windows tensor(0.1821)
cleaning windows tensor(0.1594)
bandaging tensor(0.1539)
bandaging tensor(0.1235)
cleaning windows tensor(0.1570)
cleaning windows tensor(0.1400)
cleaning windows tensor(0.1813)
breakdancing tensor(0.2235)
bandaging tensor(0.1173)
changing wheel tensor(0.1657)
changing wheel tensor(0.2003)
changing wheel tensor(0.3107)
chang

abseiling tensor(0.0757)
abseiling tensor(0.0555)
S09E22_014.mp4
blowing nose tensor(0.0635)
cleaning gutters tensor(0.0776)
clay pottery making tensor(0.1096)
beatboxing tensor(0.0544)
cleaning shoes tensor(0.2332)
dodgeball tensor(0.1465)
changing wheel tensor(0.1240)
blowing glass tensor(0.0726)
dodgeball tensor(0.0867)
cleaning shoes tensor(0.1104)
cleaning shoes tensor(0.0667)
S09E22_015.mp4
cleaning shoes tensor(0.1230)
bandaging tensor(0.1301)
bandaging tensor(0.1233)
cleaning shoes tensor(0.1452)
blowing nose tensor(0.1115)
S09E22_016.mp4
clapping tensor(0.5764)
clapping tensor(0.2860)
clapping tensor(0.1596)
clapping tensor(0.2444)
cleaning shoes tensor(0.1588)
cleaning windows tensor(0.2058)
cleaning windows tensor(0.1016)
bandaging tensor(0.1055)
bandaging tensor(0.1628)
cleaning windows tensor(0.2117)
cleaning windows tensor(0.1146)
bandaging tensor(0.1385)
bandaging tensor(0.1043)
cleaning windows tensor(0.2864)
cleaning windows tensor(0.3606)
cleaning windows tensor(0.154

abseiling tensor(0.2279)
abseiling tensor(0.1439)
changing wheel tensor(0.0746)
cleaning gutters tensor(0.0869)
brushing teeth tensor(0.0534)
clean and jerk tensor(0.0794)
answering questions tensor(0.0628)
cleaning gutters tensor(0.2350)
cleaning gutters tensor(0.0620)
abseiling tensor(0.2079)
abseiling tensor(0.1169)
abseiling tensor(0.1637)
cleaning windows tensor(0.0834)
cleaning gutters tensor(0.1083)
cleaning gutters tensor(0.1577)
abseiling tensor(0.1895)
cleaning windows tensor(0.1190)
abseiling tensor(0.1861)
abseiling tensor(0.1347)
abseiling tensor(0.0984)
S09E23_005.mp4
cleaning windows tensor(0.2996)
cleaning windows tensor(0.4211)
cleaning windows tensor(0.1766)
cleaning windows tensor(0.0819)
drinking tensor(0.0956)
air drumming tensor(0.1148)
air drumming tensor(0.0770)
clapping tensor(0.0403)
cleaning windows tensor(0.0787)
cleaning gutters tensor(0.1499)
cleaning gutters tensor(0.2730)
S09E23_006.mp4
crawling baby tensor(0.0615)
crawling baby tensor(0.0846)
cartwheeli

drawing tensor(0.1854)
cleaning shoes tensor(0.0919)
bandaging tensor(0.1079)
clean and jerk tensor(0.0762)
cartwheeling tensor(0.2510)
cleaning windows tensor(0.2006)
cleaning windows tensor(0.2346)
S09E24_001.mp4
abseiling tensor(0.2586)
abseiling tensor(0.0949)
abseiling tensor(0.0843)
abseiling tensor(0.1231)
abseiling tensor(0.1527)
abseiling tensor(0.3061)
abseiling tensor(0.3351)
abseiling tensor(0.2703)
abseiling tensor(0.1875)
abseiling tensor(0.2003)
abseiling tensor(0.2386)
cleaning windows tensor(0.0928)
breading or breadcrumbing tensor(0.5460)
abseiling tensor(0.1239)
abseiling tensor(0.1192)
abseiling tensor(0.1784)
abseiling tensor(0.2151)
abseiling tensor(0.1370)
abseiling tensor(0.2065)
blowing nose tensor(0.0836)
bandaging tensor(0.1120)
abseiling tensor(0.1276)
S09E24_002.mp4
balloon blowing tensor(0.0874)
changing wheel tensor(0.0830)
cleaning windows tensor(0.0658)
cleaning windows tensor(0.1214)
abseiling tensor(0.0931)
abseiling tensor(0.2230)
cleaning gutters te

clean and jerk tensor(0.0709)
cleaning gutters tensor(0.0852)
clean and jerk tensor(0.0597)
S09E24_026.mp4
cleaning gutters tensor(0.1348)
drinking tensor(0.0882)
bandaging tensor(0.0769)
cleaning gutters tensor(0.0834)
bandaging tensor(0.0714)
bandaging tensor(0.0834)
clapping tensor(0.0637)
bandaging tensor(0.0578)
cleaning gutters tensor(0.0730)
cleaning windows tensor(0.0666)
cleaning windows tensor(0.0644)
cleaning windows tensor(0.2500)
cleaning windows tensor(0.3452)
cleaning windows tensor(0.2352)
cleaning pool tensor(0.0994)
cleaning pool tensor(0.1236)
cleaning pool tensor(0.1369)
cleaning pool tensor(0.1048)
cleaning pool tensor(0.1136)
S09E24_027.mp4
cleaning pool tensor(0.1015)
cleaning pool tensor(0.1367)
cleaning pool tensor(0.1027)
cleaning pool tensor(0.1261)
cleaning pool tensor(0.1079)
cleaning gutters tensor(0.0856)
cleaning gutters tensor(0.1230)
cleaning gutters tensor(0.1656)
cleaning gutters tensor(0.1962)
cleaning windows tensor(0.4262)
cleaning windows tensor(

In [2]:
path_t = "../../Speech-Emotion-Recognition/datasets/tess"

In [4]:
filepath = path_t
print("processing", filepath)
assert os.path.isdir(filepath)
for file in os.listdir(filepath):
    label = file.strip('.wav').split('_')[2]
    if label in ['sad', 'angry', 'neutral', 'happy', 'disgust']: 
        file_move = os.path.join(path_r, label)
    elif label == 'ps':
        file_move = os.path.join(path_r, 'surprise')
    elif label == 'fear':
        file_move = os.path.join(path_r, 'fearful')
    print("moving", file, "to", file_move)
    if not os.path.isdir(file_move):
        os.makedirs(file_move)
    shutil.copyfile(os.path.join(filepath, file), os.path.join(file_move, file))

processing ../../Speech-Emotion-Recognition/datasets/tess
moving OAF_take_angry.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/angry
moving YAF_pike_disgust.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/disgust
moving YAF_which_neutral.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/neutral
moving OAF_kill_happy.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/happy
moving OAF_sell_fear.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/fearful
moving OAF_chat_sad.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/sad
moving YAF_cheek_ps.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/surprise
moving YAF_rag_happy.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/happy
moving OAF_hash_happy.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/happy
moving OAF_size_happy.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/happy
moving OAF_dab_angry.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/angry
mo

moving YAF_laud_fear.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/fearful
moving YAF_king_fear.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/fearful
moving YAF_hire_sad.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/sad
moving YAF_jar_angry.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/angry
moving YAF_room_ps.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/surprise
moving YAF_lot_disgust.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/disgust
moving OAF_chief_sad.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/sad
moving YAF_far_neutral.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/neutral
moving OAF_keep_disgust.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/disgust
moving OAF_void_neutral.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/neutral
moving YAF_puff_sad.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/sad
moving YAF_raid_fear.wav to ../../Speech-Emotion-Recognition/

moving YAF_cheek_angry.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/angry
moving OAF_rat_disgust.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/disgust
moving YAF_gun_sad.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/sad
moving OAF_mill_neutral.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/neutral
moving OAF_ditch_happy.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/happy
moving OAF_dead_sad.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/sad
moving YAF_bath_happy.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/happy
moving YAF_youth_disgust.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/disgust
moving OAF_mode_fear.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/fearful
moving YAF_sub_happy.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/happy
moving OAF_witch_happy.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/happy
moving YAF_moon_disgust.wav to ../../Speech-Emotion-Recogni

moving YAF_germ_disgust.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/disgust
moving YAF_date_ps.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/surprise
moving OAF_rough_fear.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/fearful
moving YAF_take_angry.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/angry
moving YAF_gaze_disgust.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/disgust
moving OAF_gap_neutral.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/neutral
moving OAF_yes_ps.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/surprise
moving OAF_lease_fear.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/fearful
moving YAF_hole_disgust.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/disgust
moving YAF_pole_neutral.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/neutral
moving OAF_phone_fear.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/fearful
moving OAF_beg_disgust.wav to ../../Speec

moving OAF_germ_ps.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/surprise
moving YAF_fail_neutral.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/neutral
moving YAF_soup_sad.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/sad
moving OAF_name_sad.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/sad
moving YAF_five_angry.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/angry
moving OAF_sheep_angry.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/angry
moving OAF_came_neutral.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/neutral
moving OAF_turn_fear.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/fearful
moving OAF_shout_sad.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/sad
moving YAF_gun_angry.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/angry
moving YAF_bath_sad.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/sad
moving OAF_date_neutral.wav to ../../Speech-Emotion-Recognition/dataset

moving YAF_came_neutral.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/neutral
moving YAF_bar_neutral.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/neutral
moving YAF_size_happy.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/happy
moving OAF_merge_disgust.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/disgust
moving OAF_limb_angry.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/angry
moving YAF_date_happy.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/happy
moving YAF_bite_ps.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/surprise
moving OAF_far_happy.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/happy
moving YAF_wife_ps.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/surprise
moving YAF_tool_fear.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/fearful
moving OAF_thin_angry.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/angry
moving OAF_youth_happy.wav to ../../Speech-Emotion-Re

moving YAF_pearl_happy.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/happy
moving YAF_lose_fear.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/fearful
moving OAF_jail_fear.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/fearful
moving OAF_pain_ps.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/surprise
moving YAF_goal_angry.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/angry
moving YAF_thumb_sad.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/sad
moving YAF_team_disgust.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/disgust
moving OAF_tip_angry.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/angry
moving YAF_hash_neutral.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/neutral
moving OAF_such_neutral.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/neutral
moving OAF_keg_angry.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/angry
moving YAF_cause_disgust.wav to ../../Speech-Emotion-Re

moving YAF_search_ps.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/surprise
moving OAF_calm_fear.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/fearful
moving OAF_goose_disgust.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/disgust
moving YAF_lore_neutral.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/neutral
moving OAF_hush_ps.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/surprise
moving YAF_bar_happy.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/happy
moving OAF_long_sad.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/sad
moving OAF_tire_ps.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/surprise
moving OAF_vine_happy.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/happy
moving YAF_hush_angry.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/angry
moving YAF_pole_ps.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/surprise
moving OAF_jar_sad.wav to ../../Speech-Emotion-Recognition

moving OAF_luck_fear.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/fearful
moving OAF_read_disgust.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/disgust
moving YAF_soap_fear.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/fearful
moving YAF_kick_fear.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/fearful
moving YAF_yearn_happy.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/happy
moving OAF_rot_ps.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/surprise
moving OAF_have_disgust.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/disgust
moving OAF_ditch_disgust.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/disgust
moving OAF_pearl_fear.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/fearful
moving YAF_whip_sad.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/sad
moving OAF_hush_fear.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/fearful
moving YAF_white_angry.wav to ../../Speech-Emotion

moving YAF_book_angry.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/angry
moving YAF_lore_fear.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/fearful
moving OAF_five_sad.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/sad
moving OAF_gas_happy.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/happy
moving OAF_chain_fear.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/fearful
moving OAF_fit_sad.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/sad
moving OAF_witch_neutral.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/neutral
moving YAF_have_happy.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/happy
moving OAF_gaze_neutral.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/neutral
moving YAF_keg_neutral.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/neutral
moving OAF_nag_neutral.wav to ../../Speech-Emotion-Recognition/datasets/ravdess/neutral
moving YAF_numb_fear.wav to ../../Speech-Emotion-Recognit

In [47]:
audios = json.load(open('../../MEmoR/data/features/audio_features.json', 'rb'))

In [48]:
list_audio = list()
for key, value in audios.items():
    value.insert(0, -1)
    value.insert(0, key)
    list_audio.append(value)

In [49]:
list_name = ['name', 'label']

for i in range(1, len(list_audio[0]) - 1):
    list_name.append(str(i))

test = pandas.DataFrame(columns=list_name, data=list_audio)
test.set_index('name', inplace=True)
test.head()

label         1         2         3         4         5  \
name                                                                    
S01E01_000+2     -1 -0.487681  1.643616  1.559166 -0.610276 -0.899613   
S01E01_000+1     -1  0.368327 -1.073846  0.584876 -1.891454 -2.181485   
S01E01_000+0     -1  0.935033  0.633743  1.571338 -0.571352 -0.845702   
S01E01_001+0     -1  0.658490 -1.378777  1.279003 -0.914935 -0.796738   
S01E01_002+1     -1  1.467682 -1.308398 -0.178871  0.459403  1.507893   

                     6         7         8         9  ...      6364      6365  \
name                                                  ...                       
S01E01_000+2 -1.090241 -0.856790 -0.625202 -0.892273  ...  0.115958  1.027125   
S01E01_000+1 -2.017179 -1.261587 -0.074902 -0.776989  ... -0.770196 -1.050085   
S01E01_000+0 -0.926902 -0.810107 -0.362317 -0.698398  ...  0.537415  0.631336   
S01E01_001+0 -0.662570 -0.016392  0.143214  0.081437  ...  1.248474  1.037824   
S01E01_002+1  1.801616  2.553402  0.988595  2.103925  ...  1.836562  1.489716   

                  6366      6367      6368      6369      6370      6371  \
name                                                                       
S01E01_000+2 -0.474039 -0.456126 -0.015859 -0.064687  0.108869 -0.484421   
S01E01_000+1 -0.383671 -0.432288 -0.004085  1.178384  0.114044  0.459518   
S01E01_000+0 -0.366233 -0.379637  0.002938  0.282560 -0.200369 -0.391455   
S01E01_001+0 -0.216602 -0.230889  0.004961 -0.214087 -0.055852  0.025668   
S01E01_002+1 -0.063776 -0.033129 -0.011182 -0.408897 -0.230709 -0.299573   

                  6372      6373  
name                              
S01E01_000+2  0.392455  0.506518  
S01E01_000+1 -0.320785 -0.289987  
S01E01_000+0  0.079904 -0.210378  
S01E01_001+0 -0.059348 -0.187772  
S01E01_002+1  0.112543 -0.235265  

[5 rows x 6374 columns]

In [50]:
path_w = '../../Speech-Emotion-Recognition/features/8-category/test_opensmile_all.csv'

test.to_csv(open(path_w, 'w'))

In [54]:
test.loc[:, ['label', '1', '2']]

label         1         2
name                                   
S01E01_000+2     -1 -0.487681  1.643616
S01E01_000+1     -1  0.368327 -1.073846
S01E01_000+0     -1  0.935033  0.633743
S01E01_001+0     -1  0.658490 -1.378777
S01E01_002+1     -1  1.467682 -1.308398
...             ...       ...       ...
S09E24_044+1     -1  0.379699 -1.191375
S09E24_044+0     -1  1.315771 -0.717025
S09E24_045+1     -1  1.313072  1.413322
S09E24_045+0     -1  0.068127 -0.310632
S09E24_046+0     -1  1.268740  1.400528

[13904 rows x 3 columns]

In [58]:
for index in test.index:
    print(index, type(index))

S01E01_000+2 <class 'str'>
S01E01_000+1 <class 'str'>
S01E01_000+0 <class 'str'>
S01E01_001+0 <class 'str'>
S01E01_002+1 <class 'str'>
S01E01_002+0 <class 'str'>
S01E01_003+2 <class 'str'>
S01E01_003+1 <class 'str'>
S01E01_003+0 <class 'str'>
S01E01_004+2 <class 'str'>
S01E01_004+5 <class 'str'>
S01E01_004+3 <class 'str'>
S01E01_004+1 <class 'str'>
S01E01_004+0 <class 'str'>
S01E01_004+6 <class 'str'>
S01E01_004+4 <class 'str'>
S01E01_005+2 <class 'str'>
S01E01_005+1 <class 'str'>
S01E01_005+0 <class 'str'>
S01E01_006+2 <class 'str'>
S01E01_006+3 <class 'str'>
S01E01_006+1 <class 'str'>
S01E01_006+0 <class 'str'>
S01E01_007+2 <class 'str'>
S01E01_007+5 <class 'str'>
S01E01_007+3 <class 'str'>
S01E01_007+1 <class 'str'>
S01E01_007+0 <class 'str'>
S01E01_007+4 <class 'str'>
S01E01_008+2 <class 'str'>
S01E01_008+5 <class 'str'>
S01E01_008+3 <class 'str'>
S01E01_008+1 <class 'str'>
S01E01_008+0 <class 'str'>
S01E01_008+7 <class 'str'>
S01E01_008+6 <class 'str'>
S01E01_008+4 <class 'str'>
S

S02E04_014+1 <class 'str'>
S02E04_014+0 <class 'str'>
S02E04_015+2 <class 'str'>
S02E04_015+1 <class 'str'>
S02E04_015+0 <class 'str'>
S02E04_016+2 <class 'str'>
S02E04_016+3 <class 'str'>
S02E04_016+1 <class 'str'>
S02E04_016+0 <class 'str'>
S02E04_016+4 <class 'str'>
S02E04_017+1 <class 'str'>
S02E04_017+0 <class 'str'>
S02E04_018+1 <class 'str'>
S02E04_018+0 <class 'str'>
S02E04_019+2 <class 'str'>
S02E04_019+5 <class 'str'>
S02E04_019+3 <class 'str'>
S02E04_019+1 <class 'str'>
S02E04_019+0 <class 'str'>
S02E04_019+6 <class 'str'>
S02E04_019+4 <class 'str'>
S02E04_020+2 <class 'str'>
S02E04_020+1 <class 'str'>
S02E04_020+0 <class 'str'>
S02E04_021+1 <class 'str'>
S02E04_021+0 <class 'str'>
S02E04_022+2 <class 'str'>
S02E04_022+3 <class 'str'>
S02E04_022+1 <class 'str'>
S02E04_022+0 <class 'str'>
S02E04_023+0 <class 'str'>
S02E04_024+2 <class 'str'>
S02E04_024+1 <class 'str'>
S02E04_024+0 <class 'str'>
S02E04_025+2 <class 'str'>
S02E04_025+1 <class 'str'>
S02E04_025+0 <class 'str'>
S

S03E07_007+2 <class 'str'>
S03E07_007+3 <class 'str'>
S03E07_007+1 <class 'str'>
S03E07_007+0 <class 'str'>
S03E07_008+2 <class 'str'>
S03E07_008+3 <class 'str'>
S03E07_008+1 <class 'str'>
S03E07_008+0 <class 'str'>
S03E07_009+1 <class 'str'>
S03E07_009+0 <class 'str'>
S03E07_010+1 <class 'str'>
S03E07_010+0 <class 'str'>
S03E07_011+1 <class 'str'>
S03E07_011+0 <class 'str'>
S03E07_012+2 <class 'str'>
S03E07_012+1 <class 'str'>
S03E07_012+0 <class 'str'>
S03E08_000+1 <class 'str'>
S03E08_000+0 <class 'str'>
S03E08_001+0 <class 'str'>
S03E08_002+1 <class 'str'>
S03E08_002+0 <class 'str'>
S03E08_003+3 <class 'str'>
S03E08_003+1 <class 'str'>
S03E08_003+0 <class 'str'>
S03E08_003+4 <class 'str'>
S03E08_004+2 <class 'str'>
S03E08_004+3 <class 'str'>
S03E08_004+1 <class 'str'>
S03E08_004+0 <class 'str'>
S03E08_005+0 <class 'str'>
S03E08_006+1 <class 'str'>
S03E08_006+0 <class 'str'>
S03E08_007+1 <class 'str'>
S03E08_007+0 <class 'str'>
S03E08_008+1 <class 'str'>
S03E08_008+0 <class 'str'>
S

S04E06_031+1 <class 'str'>
S04E06_031+0 <class 'str'>
S04E06_032+0 <class 'str'>
S04E06_033+0 <class 'str'>
S04E07_000+2 <class 'str'>
S04E07_000+1 <class 'str'>
S04E07_000+0 <class 'str'>
S04E07_001+2 <class 'str'>
S04E07_001+3 <class 'str'>
S04E07_001+1 <class 'str'>
S04E07_001+0 <class 'str'>
S04E07_002+1 <class 'str'>
S04E07_002+0 <class 'str'>
S04E07_003+2 <class 'str'>
S04E07_003+1 <class 'str'>
S04E07_003+0 <class 'str'>
S04E07_004+1 <class 'str'>
S04E07_004+0 <class 'str'>
S04E07_005+2 <class 'str'>
S04E07_005+1 <class 'str'>
S04E07_005+0 <class 'str'>
S04E07_006+2 <class 'str'>
S04E07_006+3 <class 'str'>
S04E07_006+1 <class 'str'>
S04E07_006+0 <class 'str'>
S04E07_007+2 <class 'str'>
S04E07_007+3 <class 'str'>
S04E07_007+1 <class 'str'>
S04E07_007+0 <class 'str'>
S04E07_008+1 <class 'str'>
S04E07_008+0 <class 'str'>
S04E07_009+1 <class 'str'>
S04E07_009+0 <class 'str'>
S04E07_010+1 <class 'str'>
S04E07_010+0 <class 'str'>
S04E07_011+1 <class 'str'>
S04E07_011+0 <class 'str'>
S

S05E05_013+0 <class 'str'>
S05E05_014+1 <class 'str'>
S05E05_014+0 <class 'str'>
S05E06_000+1 <class 'str'>
S05E06_000+0 <class 'str'>
S05E06_001+1 <class 'str'>
S05E06_001+0 <class 'str'>
S05E06_002+1 <class 'str'>
S05E06_002+0 <class 'str'>
S05E06_003+3 <class 'str'>
S05E06_003+1 <class 'str'>
S05E06_003+0 <class 'str'>
S05E06_003+4 <class 'str'>
S05E06_004+2 <class 'str'>
S05E06_004+1 <class 'str'>
S05E06_004+0 <class 'str'>
S05E06_005+1 <class 'str'>
S05E06_005+0 <class 'str'>
S05E06_006+1 <class 'str'>
S05E06_006+0 <class 'str'>
S05E06_007+0 <class 'str'>
S05E06_008+2 <class 'str'>
S05E06_008+3 <class 'str'>
S05E06_008+1 <class 'str'>
S05E06_008+0 <class 'str'>
S05E06_009+0 <class 'str'>
S05E06_010+2 <class 'str'>
S05E06_010+1 <class 'str'>
S05E06_010+0 <class 'str'>
S05E07_000+1 <class 'str'>
S05E07_000+0 <class 'str'>
S05E07_001+2 <class 'str'>
S05E07_001+1 <class 'str'>
S05E07_001+0 <class 'str'>
S05E07_002+1 <class 'str'>
S05E07_002+0 <class 'str'>
S05E07_003+1 <class 'str'>
S

S06E07_002+2 <class 'str'>
S06E07_002+1 <class 'str'>
S06E07_002+0 <class 'str'>
S06E07_003+2 <class 'str'>
S06E07_003+1 <class 'str'>
S06E07_003+0 <class 'str'>
S06E07_004+1 <class 'str'>
S06E07_004+0 <class 'str'>
S06E07_005+0 <class 'str'>
S06E07_006+2 <class 'str'>
S06E07_006+1 <class 'str'>
S06E07_006+0 <class 'str'>
S06E07_007+2 <class 'str'>
S06E07_007+1 <class 'str'>
S06E07_007+0 <class 'str'>
S06E07_008+1 <class 'str'>
S06E07_008+0 <class 'str'>
S06E07_009+0 <class 'str'>
S06E07_010+1 <class 'str'>
S06E07_010+0 <class 'str'>
S06E07_011+2 <class 'str'>
S06E07_011+1 <class 'str'>
S06E07_011+0 <class 'str'>
S06E07_012+1 <class 'str'>
S06E07_012+0 <class 'str'>
S06E07_013+0 <class 'str'>
S06E07_014+1 <class 'str'>
S06E07_014+0 <class 'str'>
S06E07_015+0 <class 'str'>
S06E07_016+1 <class 'str'>
S06E07_016+0 <class 'str'>
S06E07_017+0 <class 'str'>
S06E07_018+0 <class 'str'>
S06E07_019+2 <class 'str'>
S06E07_019+1 <class 'str'>
S06E07_019+0 <class 'str'>
S06E07_020+0 <class 'str'>
S

S07E07_022+3 <class 'str'>
S07E07_022+1 <class 'str'>
S07E07_022+0 <class 'str'>
S07E07_023+2 <class 'str'>
S07E07_023+1 <class 'str'>
S07E07_023+0 <class 'str'>
S07E07_024+0 <class 'str'>
S07E07_025+2 <class 'str'>
S07E07_025+1 <class 'str'>
S07E07_025+0 <class 'str'>
S07E07_026+2 <class 'str'>
S07E07_026+1 <class 'str'>
S07E07_026+0 <class 'str'>
S07E07_027+2 <class 'str'>
S07E07_027+3 <class 'str'>
S07E07_027+1 <class 'str'>
S07E07_027+0 <class 'str'>
S07E07_028+0 <class 'str'>
S07E07_029+2 <class 'str'>
S07E07_029+1 <class 'str'>
S07E07_029+0 <class 'str'>
S07E07_030+1 <class 'str'>
S07E07_030+0 <class 'str'>
S07E07_031+0 <class 'str'>
S07E07_032+2 <class 'str'>
S07E07_032+1 <class 'str'>
S07E07_032+0 <class 'str'>
S07E08_000+2 <class 'str'>
S07E08_000+3 <class 'str'>
S07E08_000+1 <class 'str'>
S07E08_000+0 <class 'str'>
S07E08_000+4 <class 'str'>
S07E08_001+1 <class 'str'>
S07E08_001+0 <class 'str'>
S07E08_002+2 <class 'str'>
S07E08_002+1 <class 'str'>
S07E08_002+0 <class 'str'>
S

S08E02_000+1 <class 'str'>
S08E02_000+0 <class 'str'>
S08E02_001+1 <class 'str'>
S08E02_001+0 <class 'str'>
S08E02_002+1 <class 'str'>
S08E02_002+0 <class 'str'>
S08E02_003+2 <class 'str'>
S08E02_003+1 <class 'str'>
S08E02_003+0 <class 'str'>
S08E02_004+0 <class 'str'>
S08E02_005+2 <class 'str'>
S08E02_005+1 <class 'str'>
S08E02_005+0 <class 'str'>
S08E02_006+2 <class 'str'>
S08E02_006+3 <class 'str'>
S08E02_006+1 <class 'str'>
S08E02_006+0 <class 'str'>
S08E02_007+1 <class 'str'>
S08E02_007+0 <class 'str'>
S08E02_008+2 <class 'str'>
S08E02_008+3 <class 'str'>
S08E02_008+1 <class 'str'>
S08E02_008+0 <class 'str'>
S08E02_009+2 <class 'str'>
S08E02_009+3 <class 'str'>
S08E02_009+1 <class 'str'>
S08E02_009+0 <class 'str'>
S08E02_010+2 <class 'str'>
S08E02_010+1 <class 'str'>
S08E02_010+0 <class 'str'>
S08E02_011+1 <class 'str'>
S08E02_011+0 <class 'str'>
S08E02_012+0 <class 'str'>
S08E02_013+1 <class 'str'>
S08E02_013+0 <class 'str'>
S08E02_014+2 <class 'str'>
S08E02_014+1 <class 'str'>
S

S09E05_006+1 <class 'str'>
S09E05_006+0 <class 'str'>
S09E05_007+2 <class 'str'>
S09E05_007+1 <class 'str'>
S09E05_007+0 <class 'str'>
S09E05_008+0 <class 'str'>
S09E05_009+2 <class 'str'>
S09E05_009+3 <class 'str'>
S09E05_009+1 <class 'str'>
S09E05_009+0 <class 'str'>
S09E05_010+1 <class 'str'>
S09E05_010+0 <class 'str'>
S09E05_011+1 <class 'str'>
S09E05_011+0 <class 'str'>
S09E05_012+2 <class 'str'>
S09E05_012+1 <class 'str'>
S09E05_012+0 <class 'str'>
S09E05_013+0 <class 'str'>
S09E05_014+2 <class 'str'>
S09E05_014+3 <class 'str'>
S09E05_014+1 <class 'str'>
S09E05_014+0 <class 'str'>
S09E05_015+2 <class 'str'>
S09E05_015+3 <class 'str'>
S09E05_015+1 <class 'str'>
S09E05_015+0 <class 'str'>
S09E05_016+0 <class 'str'>
S09E05_017+0 <class 'str'>
S09E06_000+2 <class 'str'>
S09E06_000+5 <class 'str'>
S09E06_000+3 <class 'str'>
S09E06_000+1 <class 'str'>
S09E06_000+0 <class 'str'>
S09E06_000+4 <class 'str'>
S09E06_001+2 <class 'str'>
S09E06_001+1 <class 'str'>
S09E06_001+0 <class 'str'>
S

In [59]:
df = pd.read_csv('../../Speech-Emotion-Recognition/features/8-category/test_opensmile_all.csv')
features = [str(i) for i in range(1, 6374)]
X = df.loc[:,features].values

In [65]:
df.head()

name  label         1         2         3         4         5  \
0  S01E01_000+2     -1 -0.487681  1.643616  1.559166 -0.610276 -0.899613   
1  S01E01_000+1     -1  0.368327 -1.073846  0.584876 -1.891454 -2.181485   
2  S01E01_000+0     -1  0.935033  0.633743  1.571338 -0.571352 -0.845702   
3  S01E01_001+0     -1  0.658490 -1.378777  1.279003 -0.914935 -0.796738   
4  S01E01_002+1     -1  1.467682 -1.308398 -0.178871  0.459403  1.507893   

          6         7         8  ...      6364      6365      6366      6367  \
0 -1.090241 -0.856790 -0.625202  ...  0.115958  1.027125 -0.474039 -0.456126   
1 -2.017179 -1.261587 -0.074902  ... -0.770196 -1.050085 -0.383671 -0.432288   
2 -0.926902 -0.810107 -0.362317  ...  0.537415  0.631336 -0.366233 -0.379637   
3 -0.662570 -0.016392  0.143214  ...  1.248474  1.037824 -0.216602 -0.230889   
4  1.801616  2.553402  0.988595  ...  1.836562  1.489716 -0.063776 -0.033129   

       6368      6369      6370      6371      6372      6373  
0 -0.015859 -0.064687  0.108869 -0.484421  0.392455  0.506518  
1 -0.004085  1.178384  0.114044  0.459518 -0.320785 -0.289987  
2  0.002938  0.282560 -0.200369 -0.391455  0.079904 -0.210378  
3  0.004961 -0.214087 -0.055852  0.025668 -0.059348 -0.187772  
4 -0.011182 -0.408897 -0.230709 -0.299573  0.112543 -0.235265  

[5 rows x 6375 columns]

In [66]:
scaler = joblib.load('../../Speech-Emotion-Recognition/checkpoints/SCALER_OPENSMILE.m')
test_feature = scaler.transform(X)

In [67]:
test_feature[0]

array([-1.86600557,  5.34331609,  3.05812259, ..., -2.72670302,
       -3.48042405, -2.34245459])

In [11]:
obj = DeepFace.analyze(img_path = "/data_SSD1/hliu/data_MEmoR/faces/S01E01_000/100_Sheldon.jpg", actions = ['emotion'])
print(obj["age"]," years old ",obj["dominant_race"]," ",obj["dominant_emotion"]," ", obj["gender"])

Action: emotion:   0%|          | 0/4 [00:00<?, ?it/s]


AbortedError:  Operation received an exception:Status: 2, message: could not create a descriptor for a softmax forward propagation primitive, in file tensorflow/core/kernels/mkl_softmax_op.cc:312
	 [[node model_31/softmax_24/Softmax (defined at /data_SSD1/hliu/softwares/anaconda3/envs/EmoRC/lib/python3.6/site-packages/mtcnn/mtcnn.py:342) ]] [Op:__inference_predict_function_11804]

Function call stack:
predict_function


In [21]:
filename = '../data/audios/S01E01_000.wav'

subfile = AudioSegment.from_file(filename, 'wav')

tmp = subfile[: 12080]

tmp.export('../data/audios/S01E01_000_tmp1.wav', format='wav')

tmp = subfile[12080: 14750]
tmp.export('../data/audios/S01E01_000_tmp2.wav', format='wav')

<_io.BufferedRandom name='../data/audios/S01E01_000_tmp2.wav'>

In [29]:
path_audio = '../data/audios'
path_audio_segment = '../data/audio_segments'
files_audio = sorted(os.listdir(path_audio))

path_data = '../data/data.json'
file_data = json.load(open(path_data, 'r'))

for file_audio in files_audio:
    path_file_audio = os.path.join(path_audio, file_audio)
    print('processing %s' % path_file_audio, end=', ')
    tmp_audio = AudioSegment.from_file(path_file_audio, 'wav')
    
    file_audio = file_audio.strip('.wav')
    seg_start, seg_end, start, end = \
        file_data[file_audio]["seg_start"], \
        file_data[file_audio]["seg_end"], \
        file_data[file_audio]["start"], \
        file_data[file_audio]["end"]
    seg_ori_ind = file_data[file_audio]["seg_ori_ind"]
    for index in seg_ori_ind: 
        seg_audio = tmp_audio[(seg_start[index] - start) * 1000: (seg_end[index] - start) * 1000]
        path_file_audio_segment = os.path.join(path_audio_segment, file_audio + '+' + str(index) + '.wav')
        seg_audio.export(path_file_audio_segment, format='wav')
    
    print('%d sgements processed' % len(seg_ori_ind))

processing ../data/audios/S01E01_000.wav, 3 sgements processed
processing ../data/audios/S01E01_001.wav, 1 sgements processed
processing ../data/audios/S01E01_002.wav, 2 sgements processed
processing ../data/audios/S01E01_003.wav, 3 sgements processed
processing ../data/audios/S01E01_004.wav, 7 sgements processed
processing ../data/audios/S01E01_005.wav, 3 sgements processed
processing ../data/audios/S01E01_006.wav, 4 sgements processed
processing ../data/audios/S01E01_007.wav, 6 sgements processed
processing ../data/audios/S01E01_008.wav, 8 sgements processed
processing ../data/audios/S01E01_009.wav, 6 sgements processed
processing ../data/audios/S01E01_010.wav, 4 sgements processed
processing ../data/audios/S01E01_011.wav, 6 sgements processed
processing ../data/audios/S01E01_012.wav, 5 sgements processed
processing ../data/audios/S01E01_013.wav, 4 sgements processed
processing ../data/audios/S01E01_014.wav, 6 sgements processed
processing ../data/audios/S01E01_015.wav, 3 sgements pr

processing ../data/audios/S01E04_011.wav, 4 sgements processed
processing ../data/audios/S01E04_012.wav, 1 sgements processed
processing ../data/audios/S01E04_013.wav, 4 sgements processed
processing ../data/audios/S01E04_014.wav, 2 sgements processed
processing ../data/audios/S01E04_015.wav, 2 sgements processed
processing ../data/audios/S01E04_016.wav, 2 sgements processed
processing ../data/audios/S01E04_017.wav, 2 sgements processed
processing ../data/audios/S01E04_018.wav, 4 sgements processed
processing ../data/audios/S01E04_019.wav, 1 sgements processed
processing ../data/audios/S01E04_020.wav, 1 sgements processed
processing ../data/audios/S01E04_021.wav, 3 sgements processed
processing ../data/audios/S01E04_022.wav, 2 sgements processed
processing ../data/audios/S01E04_023.wav, 2 sgements processed
processing ../data/audios/S01E04_024.wav, 6 sgements processed
processing ../data/audios/S01E04_025.wav, 4 sgements processed
processing ../data/audios/S01E04_026.wav, 1 sgements pr

processing ../data/audios/S01E08_012.wav, 2 sgements processed
processing ../data/audios/S01E08_013.wav, 2 sgements processed
processing ../data/audios/S01E08_014.wav, 2 sgements processed
processing ../data/audios/S01E08_015.wav, 2 sgements processed
processing ../data/audios/S01E08_016.wav, 3 sgements processed
processing ../data/audios/S01E08_017.wav, 4 sgements processed
processing ../data/audios/S01E08_018.wav, 4 sgements processed
processing ../data/audios/S01E08_019.wav, 2 sgements processed
processing ../data/audios/S01E08_020.wav, 5 sgements processed
processing ../data/audios/S01E08_021.wav, 6 sgements processed
processing ../data/audios/S01E08_022.wav, 4 sgements processed
processing ../data/audios/S01E08_023.wav, 4 sgements processed
processing ../data/audios/S01E08_024.wav, 3 sgements processed
processing ../data/audios/S01E08_025.wav, 5 sgements processed
processing ../data/audios/S01E08_026.wav, 3 sgements processed
processing ../data/audios/S01E08_027.wav, 4 sgements pr

processing ../data/audios/S01E13_021.wav, 3 sgements processed
processing ../data/audios/S01E13_022.wav, 2 sgements processed
processing ../data/audios/S01E13_023.wav, 6 sgements processed
processing ../data/audios/S01E13_024.wav, 1 sgements processed
processing ../data/audios/S01E13_025.wav, 5 sgements processed
processing ../data/audios/S01E13_026.wav, 2 sgements processed
processing ../data/audios/S01E13_027.wav, 2 sgements processed
processing ../data/audios/S01E13_028.wav, 1 sgements processed
processing ../data/audios/S01E13_029.wav, 2 sgements processed
processing ../data/audios/S01E13_030.wav, 5 sgements processed
processing ../data/audios/S01E13_031.wav, 2 sgements processed
processing ../data/audios/S01E13_032.wav, 2 sgements processed
processing ../data/audios/S01E14_000.wav, 2 sgements processed
processing ../data/audios/S01E14_001.wav, 4 sgements processed
processing ../data/audios/S01E14_002.wav, 4 sgements processed
processing ../data/audios/S01E14_003.wav, 9 sgements pr

processing ../data/audios/S02E02_009.wav, 4 sgements processed
processing ../data/audios/S02E02_010.wav, 2 sgements processed
processing ../data/audios/S02E02_011.wav, 5 sgements processed
processing ../data/audios/S02E02_012.wav, 2 sgements processed
processing ../data/audios/S02E02_013.wav, 3 sgements processed
processing ../data/audios/S02E02_014.wav, 3 sgements processed
processing ../data/audios/S02E02_015.wav, 3 sgements processed
processing ../data/audios/S02E02_016.wav, 1 sgements processed
processing ../data/audios/S02E02_017.wav, 1 sgements processed
processing ../data/audios/S02E03_000.wav, 4 sgements processed
processing ../data/audios/S02E03_001.wav, 3 sgements processed
processing ../data/audios/S02E03_002.wav, 2 sgements processed
processing ../data/audios/S02E03_003.wav, 1 sgements processed
processing ../data/audios/S02E03_004.wav, 3 sgements processed
processing ../data/audios/S02E03_005.wav, 2 sgements processed
processing ../data/audios/S02E03_006.wav, 3 sgements pr

...

processing ../data/audios/S09E08_016.wav, 3 sgements processed
processing ../data/audios/S09E08_017.wav, 3 sgements processed
processing ../data/audios/S09E08_018.wav, 2 sgements processed
processing ../data/audios/S09E08_019.wav, 2 sgements processed
processing ../data/audios/S09E08_020.wav, 3 sgements processed
processing ../data/audios/S09E08_021.wav, 4 sgements processed
processing ../data/audios/S09E08_022.wav, 4 sgements processed
processing ../data/audios/S09E08_023.wav, 4 sgements processed
processing ../data/audios/S09E08_024.wav, 1 sgements processed
processing ../data/audios/S09E08_025.wav, 2 sgements processed
processing ../data/audios/S09E08_026.wav, 1 sgements processed
processing ../data/audios/S09E08_027.wav, 1 sgements processed
processing ../data/audios/S09E08_028.wav, 1 sgements processed
processing ../data/audios/S09E08_029.wav, 2 sgements processed
processing ../data/audios/S09E08_030.wav, 2 sgements processed
processing ../data/audios/S09E09_000.wav, 3 sgements pr

processing ../data/audios/S09E12_017.wav, 2 sgements processed
processing ../data/audios/S09E12_018.wav, 1 sgements processed
processing ../data/audios/S09E12_019.wav, 2 sgements processed
processing ../data/audios/S09E12_020.wav, 3 sgements processed
processing ../data/audios/S09E12_021.wav, 4 sgements processed
processing ../data/audios/S09E12_022.wav, 1 sgements processed
processing ../data/audios/S09E12_023.wav, 5 sgements processed
processing ../data/audios/S09E12_024.wav, 3 sgements processed
processing ../data/audios/S09E12_025.wav, 3 sgements processed
processing ../data/audios/S09E12_026.wav, 2 sgements processed
processing ../data/audios/S09E12_027.wav, 3 sgements processed
processing ../data/audios/S09E12_028.wav, 3 sgements processed
processing ../data/audios/S09E12_029.wav, 2 sgements processed
processing ../data/audios/S09E12_030.wav, 4 sgements processed
processing ../data/audios/S09E12_031.wav, 2 sgements processed
processing ../data/audios/S09E12_032.wav, 2 sgements pr

processing ../data/audios/S09E15_043.wav, 4 sgements processed
processing ../data/audios/S09E15_044.wav, 2 sgements processed
processing ../data/audios/S09E15_045.wav, 3 sgements processed
processing ../data/audios/S09E15_046.wav, 3 sgements processed
processing ../data/audios/S09E15_047.wav, 2 sgements processed
processing ../data/audios/S09E15_048.wav, 1 sgements processed
processing ../data/audios/S09E15_049.wav, 2 sgements processed
processing ../data/audios/S09E15_050.wav, 4 sgements processed
processing ../data/audios/S09E15_051.wav, 1 sgements processed
processing ../data/audios/S09E15_052.wav, 1 sgements processed
processing ../data/audios/S09E16_000.wav, 2 sgements processed
processing ../data/audios/S09E16_001.wav, 3 sgements processed
processing ../data/audios/S09E16_002.wav, 4 sgements processed
processing ../data/audios/S09E16_003.wav, 1 sgements processed
processing ../data/audios/S09E16_004.wav, 2 sgements processed
processing ../data/audios/S09E16_005.wav, 5 sgements pr

processing ../data/audios/S09E19_002.wav, 3 sgements processed
processing ../data/audios/S09E19_003.wav, 2 sgements processed
processing ../data/audios/S09E19_004.wav, 2 sgements processed
processing ../data/audios/S09E19_005.wav, 1 sgements processed
processing ../data/audios/S09E19_006.wav, 4 sgements processed
processing ../data/audios/S09E19_007.wav, 2 sgements processed
processing ../data/audios/S09E19_008.wav, 2 sgements processed
processing ../data/audios/S09E19_009.wav, 4 sgements processed
processing ../data/audios/S09E19_010.wav, 2 sgements processed
processing ../data/audios/S09E19_011.wav, 1 sgements processed
processing ../data/audios/S09E19_012.wav, 3 sgements processed
processing ../data/audios/S09E19_013.wav, 4 sgements processed
processing ../data/audios/S09E19_014.wav, 2 sgements processed
processing ../data/audios/S09E19_015.wav, 4 sgements processed
processing ../data/audios/S09E19_016.wav, 2 sgements processed
processing ../data/audios/S09E19_017.wav, 2 sgements pr

processing ../data/audios/S09E23_003.wav, 3 sgements processed
processing ../data/audios/S09E23_004.wav, 5 sgements processed
processing ../data/audios/S09E23_005.wav, 4 sgements processed
processing ../data/audios/S09E23_006.wav, 1 sgements processed
processing ../data/audios/S09E23_007.wav, 4 sgements processed
processing ../data/audios/S09E23_008.wav, 2 sgements processed
processing ../data/audios/S09E23_009.wav, 3 sgements processed
processing ../data/audios/S09E23_010.wav, 2 sgements processed
processing ../data/audios/S09E23_011.wav, 2 sgements processed
processing ../data/audios/S09E23_012.wav, 4 sgements processed
processing ../data/audios/S09E23_013.wav, 2 sgements processed
processing ../data/audios/S09E23_014.wav, 2 sgements processed
processing ../data/audios/S09E23_015.wav, 4 sgements processed
processing ../data/audios/S09E23_016.wav, 5 sgements processed
processing ../data/audios/S09E23_017.wav, 4 sgements processed
processing ../data/audios/S09E23_018.wav, 2 sgements pr